In [1]:
import collections
import numpy as np
import pandas as pd
import re

import matplotlib.pyplot as plt
from sklearn.decomposition import PCA
from sklearn.preprocessing import MinMaxScaler

from gensim.parsing.preprocessing import remove_stopwords
from nltk.stem import PorterStemmer
from nltk.tokenize import word_tokenize
from nltk.tokenize import RegexpTokenizer
import plotly.express as px

### Representation of headlines with labels in vector space - used vector space representations to represent headlines category labels. 
1. Developed a vocabulary of all words used in the headlines
2. The amount of usage of each word in each category has been updated.
3. Data were scaled by category.
4. Transformed into two-dimensional space using PCA. 
5. A scatter plot was drawn to represent the data.


#### Data from https://www.kaggle.com/code/ronikdedhia/news-category-prediction/data

In [2]:
data = pd.read_json('../data/News_Category_Dataset_v3.json', lines=True)

In [3]:
data.head()

link  \
0  https://www.huffpost.com/entry/covid-boosters-...   
1  https://www.huffpost.com/entry/american-airlin...   
2  https://www.huffpost.com/entry/funniest-tweets...   
3  https://www.huffpost.com/entry/funniest-parent...   
4  https://www.huffpost.com/entry/amy-cooper-lose...   

                                            headline   category  \
0  Over 4 Million Americans Roll Up Sleeves For O...  U.S. NEWS   
1  American Airlines Flyer Charged, Banned For Li...  U.S. NEWS   
2  23 Of The Funniest Tweets About Cats And Dogs ...     COMEDY   
3  The Funniest Tweets From Parents This Week (Se...  PARENTING   
4  Woman Who Called Cops On Black Bird-Watcher Lo...  U.S. NEWS   

                                   short_description               authors  \
0  Health experts said it is too early to predict...  Carla K. Johnson, AP   
1  He was subdued by passengers and crew when he ...        Mary Papenfuss   
2  "Until you have a dog you don't understand wha...         Elyse Wanshel   
3  "Accidentally put grown-up toothpaste on my to...      Caroline Bologna   
4  Amy Cooper accused investment firm Franklin Te...        Nina Golgowski   

        date  
0 2022-09-23  
1 2022-09-23  
2 2022-09-23  
3 2022-09-23  
4 2022-09-22

In [4]:
data.category.value_counts()

POLITICS          35602
WELLNESS          17945
ENTERTAINMENT     17362
TRAVEL             9900
STYLE & BEAUTY     9814
PARENTING          8791
HEALTHY LIVING     6694
QUEER VOICES       6347
FOOD & DRINK       6340
BUSINESS           5992
COMEDY             5400
SPORTS             5077
BLACK VOICES       4583
HOME & LIVING      4320
PARENTS            3955
THE WORLDPOST      3664
WEDDINGS           3653
WOMEN              3572
CRIME              3562
IMPACT             3484
DIVORCE            3426
WORLD NEWS         3299
MEDIA              2944
WEIRD NEWS         2777
GREEN              2622
WORLDPOST          2579
RELIGION           2577
STYLE              2254
SCIENCE            2206
TECH               2104
TASTE              2096
MONEY              1756
ARTS               1509
ENVIRONMENT        1444
FIFTY              1401
GOOD NEWS          1398
U.S. NEWS          1377
ARTS & CULTURE     1339
COLLEGE            1144
LATINO VOICES      1130
CULTURE & ARTS     1074
EDUCATION       

In [5]:
def punctioation_fix(sentence):  
    tokenizer = RegexpTokenizer(r'\w+')
    words_list = tokenizer.tokenize(sentence.lower())
    return words_list

In [6]:
def words_stemming(words_list):    
    ps = PorterStemmer()
    stem_words = [ps.stem(word) for word in words_list]
    return stem_words

In [7]:
def reduce_stop_words(words_list):
    text = ' '.join(words_list)
    filtered_sentence = remove_stopwords(text)
    return filtered_sentence.split()

In [8]:
def adjust_headline(sentence):    
    words_list = punctioation_fix(sentence)
    
    words_list = [word for word in words_list if len(word) > 1]        
    
    words_list = words_stemming(words_list)
    
    words_list = reduce_stop_words(words_list)
    
    return ' '.join(words_list)

In [9]:
def create_vocabulary(data, label_column, data_column):
    list_of_headlines = data[data_column].apply(adjust_headline).tolist()
    set_of_words = set([word for headline in list_of_headlines for word in headline.split()])

    columns = data[label_column].unique().tolist()
    columns =  [col.lower().replace('&', 'n').replace(' ', '_').replace('.', '') for col in columns]

    columns_dict = {i: col for i, col in enumerate(columns)}
    columns_dict['index'] = 'word'
    df = pd.DataFrame(index=set_of_words , columns=np.arange(len(columns))).reset_index().rename(columns=columns_dict).fillna(0)
    
    return df

In [10]:
def update_category_values(df, data, label_column, text_column):
    for cat in data[label_column].unique():
        headlines = data.loc[data[label_column]==cat, text_column].to_list()
        words_list = [word for headline in headlines for word in adjust_headline(headline).split()]
        words_dict = collections.Counter(words_list)
        
        adjusted_cat = cat.lower().replace('&', 'n').replace(' ', '_').replace('.', '')
        for word, value in words_dict.items():
            df.loc[df["word"] == word, adjusted_cat] = value
            
    return df

### 1. Vocabulary Creation

In [11]:
words_vector_df = create_vocabulary(data, 'category', 'headline')

### 2. Update vocabulary with words counts

In [12]:
words_vector_df = update_category_values(words_vector_df, data, 'category', 'headline')

### 3. Scale the data

In [13]:
scaler = MinMaxScaler()
scaled_vector_df = scaler.fit_transform(words_vector_df.select_dtypes(include=np.number))
scaled_vector_df

array([[0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.0017762 , 0.0032077 , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.00080192, ..., 0.        , 0.        ,
        0.        ],
       ...,
       [0.        , 0.        , 0.00080192, ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.0006192 ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ]])

### 4. Transpose the data

In [14]:
index_vector = words_vector_df['word']
columns = words_vector_df.columns[1:]
scaled_vector_df = pd.DataFrame(scaled_vector_df, index=index_vector, columns=columns)
categories_vector_df = scaled_vector_df.T
categories_vector_df.head()

word            asynchron       sat  shockingli  ayman    carrey  alspaugh  \
us_news               0.0  0.000000    0.000000    0.0  0.013333       0.0   
comedy                0.0  0.001776    0.000000    0.0  0.002664       0.0   
parenting             0.0  0.003208    0.000802    0.0  0.000000       0.0   
world_news            0.0  0.000000    0.000000    0.0  0.000000       0.0   
culture_n_arts        0.0  0.000000    0.000000    0.0  0.000000       0.0   

word                butt  budoff  agy  brosnan  ...  natti  rothschild  fore  \
us_news         0.000000     0.0  0.0      0.0  ...    0.0         0.0   0.0   
comedy          0.003552     0.0  0.0      0.0  ...    0.0         0.0   0.0   
parenting       0.002406     0.0  0.0      0.0  ...    0.0         0.0   0.0   
world_news      0.000000     0.0  0.0      0.0  ...    0.0         0.0   0.0   
culture_n_arts  0.006579     0.0  0.0      0.0  ...    0.0         0.0   0.0   

word              wodkin  rigatoni  1939  extortionist  momnesia  detritu  \
us_news         0.000000       0.0   0.0      0.000000  0.000000      0.0   
comedy          0.000000       0.0   0.0      0.000000  0.000000      0.0   
parenting       0.000802       0.0   0.0      0.000802  0.000802      0.0   
world_news      0.000000       0.0   0.0      0.000000  0.000000      0.0   
culture_n_arts  0.000000       0.0   0.0      0.000000  0.000000      0.0   

word            jeffersonian  
us_news                  0.0  
comedy                   0.0  
parenting                0.0  
world_news               0.0  
culture_n_arts           0.0  

[5 rows x 39767 columns]

### 5. Using PCA to convert the table into 2 dimension table

In [15]:
pca = PCA(n_components=2)
categories_2d_arr = pca.fit_transform(categories_vector_df)
categories_2d_df = pd.DataFrame(categories_2d_arr, index=categories_vector_df.index, columns=['x', 'y'])

In [16]:
fig = px.scatter(x=categories_2d_df['x'], y=categories_2d_df['y'], text=categories_2d_df.index, width=1000, height=500)
fig.show()

### PCA for words + scatter plot

In [17]:
pca = PCA(n_components=2)
words_2d_arr = pca.fit_transform(scaled_vector_df)
words_2d_df = pd.DataFrame(words_2d_arr, index=scaled_vector_df.index, columns=['x', 'y'])

In [18]:
fig = px.scatter(x=words_2d_df['x'], y=words_2d_df['y'], text=words_2d_df.index, width=1000, height=500)
fig.show()